In [3]:
# imports
import os
from dotenv import load_dotenv
from openai import OpenAI
import gradio as gr
import json

# Load environment variables in a file called .env
load_dotenv(override=True)
openai_api_key = os.getenv('OPENAI_API_KEY')
anthropic_api_key = os.getenv('ANTHROPIC_API_KEY')
google_api_key = os.getenv('GOOGLE_API_KEY')

# Initialize
openai = OpenAI()
MODEL = 'gpt-4o-mini'

# Real listing-specific information
listing_info = {
    "vehicles": [
        {
            "id": "vehicle1",
            "name": "2024 Chevrolet Equinox LS FWD (Sport Edition)",
            "type": "SUV",
            "seats": 5,
            "features": [
                "Automatic transmission",
                "AUX input",
                "Backup camera",
                "Bluetooth",
                "Keyless entry",
                "Toll pass (SunPass enabled)",
                "USB charger",
                "USB input",
                "Must be 21+ to book"
            ],
            "daily_rate": "See Turo listing",
            "mileage_limit": "Unlimited",
            "fuel_type": "Gasoline",
            "additional_notes": "Includes toll pass S/N 0729884410104. Please return with same fuel level or opt for prepaid refuel. No smoking, pets, or unauthorized drivers. $25 fee for unauthorized cancellation prior to start."
        }
    ],
    "parking_locations": {
        "airport": {
            "address": "7640 Narcoossee Rd, Orlando, FL 32822",
            "instructions": "Pickup and drop-off at OMNI Airport Parking. Use lockbox code sent via Turo app 30 minutes before pickup. Free 24/7 shuttle service to/from MCO available.",
            "shuttle": "Free 24/7 shuttle runs between MCO and OMNI Parking. Details provided before trip."
        }
    },
    "pickup_process": "Receive lockbox code via Turo app 30 minutes before pickup. Use the code to access keys. Drop off at same location.",
    "license_requirements": "Only listed drivers with valid licenses may operate the vehicle. Upload your license via the Turo app at least 24 hours before your trip. International licenses require a passport.",
    "contact_info": {
        "host": {
            "name": "MM Services",
            "phone": "Not publicly shared; use Turo messaging",
            "response_time": "Usually within 30 minutes"
        }
    },
    "cancellation_policy": "$25 cancellation fee applies if canceled before trip starts. Turo cancellation rules apply after trip starts.",
    "insurance_options": {
        "basic": "State minimum liability coverage, physical damage up to actual cash value with $3,000 deductible",
        "standard": "State minimum liability coverage, physical damage up to actual cash value with $500 deductible",
        "premium": "State minimum liability coverage, physical damage up to actual cash value with $0 deductible"
    },
    "extras": {
        "Child safety seat": "$20/trip - 2 available",
        "Prepaid refuel": "$50/trip - Return at any fuel level",
        "Cooler": "$20/trip - 1 available"
    },
    "guidelines": {
        "smoking": "No smoking. Cleaning fees apply per Turo policy.",
        "pets": "No pets. Cleaning fees apply per Turo policy.",
        "vehicle_use": "No racing, off-roading, or reckless driving. Violations incur $150+ fee.",
        "fueling": "Return with same fuel level unless prepaid refuel is selected.",
        "tolls": "Toll charges billed 30-90 days post-trip using SunPass.",
        "airport": "Do not use terminal parking. Use OMNI lot and shuttle."
    },
    "reviews": [
        {"user": "Wendy", "comment": "The pick up and drop was super nice... Host is very quick to respond and easy to communicate with."},
        {"user": "Ariel", "comment": "The car was clean and ready to go. Clear directions on pickup. Great host."},
        {"user": "Marco", "comment": "Great host! Easy instructions. Highly recommend."}
    ]
}

# Define system message
system_message = f"""You are a helpful assistant for a Turo car sharing business. Your role is to help hosts and co-hosts 
communicate effectively with customers. Provide relevant information about the hosts' car listings,
address customer queries professionally, and offer guidance on important topics.

LISTING INFORMATION:
{json.dumps(listing_info, indent=2)}

Use the above listing information to answer customer questions. Be specific when referencing vehicle details,
parking locations, and policies. For example, if someone asks about airport parking, provide the exact address
and shuttle information from the listing data. If they ask about a specific vehicle, provide details for that 
vehicle only. Always be helpful, courteous, and informative.

Key topics to address:
- Parking locations and directions
- Airport shuttle services and pickup procedures  
- License upload requirements and verification process
- Vehicle features and specifications
- Booking policies, extensions, and modifications
- Check-in and check-out procedures
- Fueling requirements and recommendations
- Mileage limits and overage fees
- Cleaning expectations and fees
- Emergency contacts and roadside assistance"""

# Chat function
def chat(message, history):
    relevant_system_message = system_message
    message_lower = message.lower()

    if 'insurance' in message_lower:
        relevant_system_message += "\nProvide specific details about our insurance options."

    elif 'cancel' in message_lower:
        relevant_system_message += "\nReference the cancellation policy."

    elif 'chevrolet' in message_lower or 'equinox' in message_lower:
        relevant_system_message += "\nThe customer is asking about the 2024 Chevrolet Equinox. Provide specific details."

    elif 'airport' in message_lower or 'parking' in message_lower:
        relevant_system_message += "\nInclude specific parking location and shuttle details."

    elif 'pickup' in message_lower or 'shuttle' in message_lower:
        relevant_system_message += "\nProvide exact pickup process and shuttle details."

    elif 'license' in message_lower or 'verification' in message_lower:
        relevant_system_message += "\nExplain license requirements clearly."

    elif 'contact' in message_lower or 'host' in message_lower:
        relevant_system_message += "\nShare host contact details from the listing."

    messages = [{"role": "system", "content": relevant_system_message}] + history + [{"role": "user", "content": message}]
    stream = openai.chat.completions.create(model=MODEL, messages=messages, stream=True)

    response = ""
    for chunk in stream:
        response += chunk.choices[0].delta.content or ''
        yield response

# Launch the chat interface
if __name__ == "__main__":
    gr.ChatInterface(
    fn=chat,
    type="messages",
    title="🚗 MM Services – Turo Rental Assistant",
    description="""
    👋 Welcome to MM Services!<br>
    Need help with your booking, pickup, airport shuttle, or car details? Just ask me!
    I’m available 24/7 to assist with anything related to your trip.
    """,
    theme="soft"
).launch(share=True)

* Running on local URL:  http://127.0.0.1:7862
* Running on public URL: https://213128f5ad0e0bb5e6.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)
